# Inspector

#### What is inspector ?  
   Vai_q_pytorch provides a function called inspector to help users diagnose neural network (NN) models under different device architectures. The inspector can predict target device assignments based on hardware constraints.The generated inspection report can be used to guide  users to modify or optimize the NN model, greatly reducing the difficulty and time of deployment. It is recommended to inspect float models before quantization.

In [1]:
import torch

import sys
import os
os.environ["CUDA_VISIBLE_DEVICES"]="0"

device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

if torch.cuda.is_available():
    print("Available GPUs:", torch.cuda.device_count())
    for i in range(torch.cuda.device_count()):
        print(f"GPU {i}: {torch.cuda.get_device_name(i)}")
else:
    print("No GPUs available, CPU {} ".format(device))

yolov5_dir = '/workspace/YOLO/YOLOv5'
sys.path.append(yolov5_dir)

from models.common import DetectMultiBackend

Available GPUs: 1
GPU 0: NVIDIA GeForce RTX 3080


In [2]:
# Import inspector API
# 
# Note:
# You can ignore warning message related with XIR. 
# The inspector relies on 'vai_utf' package. In conda env vitis-ai-pytorch in Vitis-AI docker, vai_utf is ready. But if vai_q_pytorch is installed by source code, it needs to install vai_utf in advance.
from pytorch_nndct import Inspector


[VAIQ_NOTE]: Loading NNDCT kernels...


In [3]:
model_dir = '/workspace/jupyter_notebooks/VAI_2.5/dms_yolov5n/dms_yolov5nLeaky.pt'

In [4]:
# Define a toy neural network
# model = torch.hub.load('.', 'custom', path=model_dir, source='local', autoshape=False)  # Load custom model from local path, ensure reloading is controlled
model = DetectMultiBackend(model_dir, device=device) # Load custom model from local path, ensure reloading is controlled

Fusing layers... 
YOLOv5n-LeakyReLU summary: 157 layers, 1771342 parameters, 0 gradients


In [5]:
from torchinfo import summary
summary(model, (1, 3, 480, 480))  # Display model summary for specified input size

Layer (type:depth-idx)                                  Output Shape              Param #
DetectMultiBackend                                      [1, 42, 60, 60]           --
├─DetectionModel: 1-1                                   [1, 42, 60, 60]           --
│    └─Sequential: 2-1                                  --                        --
│    │    └─Conv: 3-1                                   [1, 16, 240, 240]         (1,744)
│    │    └─C3: 3-109                                   --                        (recursive)
│    │    └─Conv: 3-3                                   [1, 32, 120, 120]         (4,640)
│    │    └─C3: 3-109                                   --                        (recursive)
│    │    └─C3: 3-5                                     [1, 32, 120, 120]         (4,704)
│    │    └─C3: 3-109                                   --                        (recursive)
│    │    └─C3: 3-13                                    --                        (recursive)
│    │   

In [6]:
# Specify a target name or fingerprint you want to deploy on
target = "DPUCZDX8G_ISA1_B4096"
# Initialize inspector with target
inspector = Inspector(target)


[VAIQ_NOTE]: =>Inspector is initialized successfully with target:
name: DPUCZDX8G_ISA1_B4096
type: DPUCZDX8G
isa_version: 1


In [7]:
# Start to inspect the float model
# Note: visualization of inspection results relies on the dot engine.If you don't install dot successfully, set 'image_format = None' when inspecting.
dummy_input = torch.randn([1, 3, 480, 480], device=device) 

inspector.inspect(model, (dummy_input,), device=device, output_dir="inspect", image_format="png") 


[VAIQ_NOTE]: =>Start to inspect model...

[VAIQ_NOTE]: =>Quant Module is in 'cuda'.

[VAIQ_NOTE]: =>Parsing DetectMultiBackend...

[VAIQ_NOTE]: Start to trace model...

[VAIQ_NOTE]: Finish tracing.

[VAIQ_NOTE]: Processing ops...


██████████████████████████████████████████████████| 144/144 [00:00<00:00, 1198.19it/s, OpInfo: name = return_0, type = Return]                                                        


[VAIQ_NOTE]: =>Doing weights equalization...

[VAIQ_NOTE]: =>Quantizable module is generated.(inspect/DetectMultiBackend.py)



[VAIQ_NOTE]: All the operators are assigned to the DPU(see more details in 'inspect/inspect_DPUCZDX8G_ISA1_B4096.txt')

[VAIQ_NOTE]: Dot image is generated.(inspect/inspect_DPUCZDX8G_ISA1_B4096.png)

[VAIQ_NOTE]: =>Finish inspecting.


##### Inspection result anaysis:
1. Layers assigned to the CPU are shown in <font color=red>red circle</font> in the dot image. The reasons for being allocated to the CPU are shown in the column of hardware constraints.
2. The target device of an input node is determined by its consumer.
3. Due to data layout difference between Pytorch('NCHW') and XIR('NHWC'), if quantizer inserts some permutes(which the node message in inspect file will inform us about), these permutes may prevent the entire model from being deployed to the target device. Sometimes, we can cancel out this automatically inserted permute by inserting a permute in the original float model, sometimes, we can't.
4. If you want more details about the inspection, see the inspection report under the output directory you specified.
5. The dot image can help you to analyze inspection result in a more intuitive way. "svg" and "png" format are both supported.


In [8]:
# Show the dot image
from IPython.display import Image
Image('inspect/inspect_DPUCZDX8G_ISA1_B4096.png')

##### How to deploy this entire model on DPU:
1. Find the location of CPU operations in original model. All the details of operations are shown in inspect_{target}.txt, including source range, points to a source which is a stack track and helps to find the exact location of this operation in source code. Take resize op as a example, from source range, we can find the location of resize op in #3 input block line 11.  
node name: ToyModel::ToyModel/Upsample[upsample]/input.3  
...  
op type: resize  
...  
source range:  
...  
<font color=red>ipython-input-3-7ec1fc6b678f(11): forward</font>  
...

2. Modify the original model according to the hardware constrains message and try to cancel out the permute inserted by quantizer with by inserting a permute in the original float model(more details see hints in inspect_{target}.txt)

# Quantizer

#### What is quantizer ?  
   The inference process is computationally intensive and requires a high memory bandwidth to satisfy the low-latency and high-throughput requirements of Edge applications.
Quantization and channel pruning techniques address these challenges while simultaneously achieving optimal performance and high energy efficiency with minimal degradation in accuracy. Through quantization, integer computing units become viable, and weights and activations can be represented with reduced precision.

In [9]:
from pytorch_nndct.apis import torch_quantizer

In [10]:
quant_mode = 'calib'
quantizer = torch_quantizer(quant_mode, model, dummy_input)

quant_model = quantizer.quant_model


[VAIQ_NOTE]: Quant config file is empty, use default quant configuration

[VAIQ_NOTE]: Quantization calibration process start up...

[VAIQ_NOTE]: =>Quant Module is in 'cuda'.

[VAIQ_NOTE]: =>Parsing DetectMultiBackend...

[VAIQ_NOTE]: Start to trace model...

[VAIQ_NOTE]: Finish tracing.

[VAIQ_NOTE]: Processing ops...


██████████████████████████████████████████████████| 144/144 [00:00<00:00, 1184.48it/s, OpInfo: name = return_0, type = Return]                                                        



[VAIQ_NOTE]: =>Doing weights equalization...

[VAIQ_NOTE]: =>Quantizable module is generated.(quantize_result/DetectMultiBackend.py)

[VAIQ_NOTE]: =>Get module with quantization.


In [11]:
# Forward pass
quantizer.quant_model(dummy_input)

# export the quantization results
quantizer.export_quant_config()


[VAIQ_NOTE]: =>Get module with quantization.

[VAIQ_NOTE]: =>Exporting quant config.(quantize_result/quant_info.json)


In [12]:
quant_mode = 'test'
# quantizer = torch_quantizer(quant_mode, model, dummy_input, device=device, bitwidth=8, target=target)
quantizer = torch_quantizer(quant_mode, model, dummy_input)
quant_model = quantizer.quant_model


[VAIQ_NOTE]: Quant config file is empty, use default quant configuration

[VAIQ_NOTE]: Quantization test process start up...

[VAIQ_NOTE]: =>Quant Module is in 'cuda'.

[VAIQ_NOTE]: =>Parsing DetectMultiBackend...

[VAIQ_NOTE]: Start to trace model...

[VAIQ_NOTE]: Finish tracing.

[VAIQ_NOTE]: Processing ops...


██████████████████████████████████████████████████| 144/144 [00:00<00:00, 1184.38it/s, OpInfo: name = return_0, type = Return]                                                        



[VAIQ_NOTE]: =>Doing weights equalization...

[VAIQ_NOTE]: =>Quantizable module is generated.(quantize_result/DetectMultiBackend.py)

[VAIQ_NOTE]: =>Get module with quantization.


In [13]:
# Forward pass 수행
quantizer.quant_model(dummy_input)

quantizer.export_xmodel(deploy_check=False)


[VAIQ_NOTE]: =>Get module with quantization.

[VAIQ_NOTE]: =>Converting to xmodel ...

[VAIQ_NOTE]: =>Successfully convert 'DetectMultiBackend' to xmodel.(quantize_result/DetectMultiBackend_int.xmodel)


### Quantize done
next process is complie .xmodel
```
vai_c_xir -x /PATH/TO/quantized.xmodel -a /PATH/TO/arch.json -o /OUTPUTPATH -n netname
```

In [14]:
!vai_c_xir -x ./quantize_result/DetectMultiBackend_int.xmodel -a /opt/vitis_ai/compiler/arch/DPUCZDX8G/KV260/arch.json -o ./compile/ -n dms_yolov5Leaky

**************************************************
* VITIS_AI Compilation - Xilinx Inc.
**************************************************
[UNILOG][INFO] Compile mode: dpu
[UNILOG][INFO] Debug mode: function
[UNILOG][INFO] Target architecture: DPUCZDX8G_ISA1_B4096
[UNILOG][INFO] Graph name: DetectMultiBackend, with op num: 448
[UNILOG][INFO] Begin to compile...
[UNILOG][INFO] Total device subgraph number 5, DPU subgraph number 1
[UNILOG][INFO] Compile done.
[UNILOG][INFO] The meta json is saved to "/workspace/jupyter_notebooks/VAI_2.5/dms_yolov5n/./compile/meta.json"
[UNILOG][INFO] The compiled xmodel is saved to "/workspace/jupyter_notebooks/VAI_2.5/dms_yolov5n/./compile//dms_yolov5Leaky.xmodel"
[UNILOG][INFO] The compiled xmodel's md5sum is c1738053bb22e05edc92fc14fdf4d17d, and has been saved to "/workspace/jupyter_notebooks/VAI_2.5/dms_yolov5n/./compile/md5sum.txt"
